# Analysing Trained detectors

## Importing libraries

In [61]:
import gc
import os
import sys
import math
import glob
import tqdm
import random
import numpy as np
from tqdm import tqdm
import time 
from time import sleep

In [62]:
import pandas as pd
import xml.etree.ElementTree as ET

In [63]:
import cv2
import dlib
from imutils import face_utils
from skimage.feature import hog
from skimage import data,exposure

In [64]:
import matplotlib 
%matplotlib inline
import matplotlib.pyplot as plt

In [65]:
from ipywidgets import widgets, interactive, fixed

## Paths

In [66]:
path_openface_xml = '/media/amogh/Stuff/OpenFace_Outputs/Openface_outputs/oface_combined_csv/openface_404_folders_75_confidence.xml'

In [67]:
path_detector_1_xml = '/home/amogh/cmu/detect_faces/custom_hog_output_1523.xml'

In [68]:
path_detector_2_xml = '/home/amogh/cmu/detect_faces/custom_hog_output_2523.xml'

In [69]:
path_detector_3_xml = '/home/amogh/cmu/detect_faces/custom_hog_output_3523.xml'

## Computation functions for rectangle

In [70]:
def box_percent_covered (a,b):
    inner = a.intersect(b).area()
    if inner == 0:
        return 0
    return max(inner/a.area(), inner/b.area())

In [71]:
def drect_add(a,b):
    """
    Being able to add two drectangles, as addition is not available in the version of dlib in anaconda environment.
    """
    
    return dlib.drectangle(min(a.left(),b.left()),min(a.top(),b.top()),max(a.right(),b.right()),max(a.bottom(),b.bottom()))

In [72]:
def intersect(a,b,iou_thresh=0.5,percent_covered_thresh=1.0):
    
    inner = a.intersect(b).area()
    if (inner == 0):
        return False
    
    outer = drect_add(a,b).area()
    print("inner,outer,a.area,b.area: ", inner, outer, a.area(),b.area())
    if (inner/outer > iou_thresh or 
        inner/a.area() > percent_covered_thresh or 
        inner/b.area() > percent_covered_thresh):
        return True
    else:
        return False

In [73]:
a = dlib.drectangle(2,1,4.5,3)
b = dlib.drectangle(3,1,5,3)

In [74]:
type(max(1.,2.))

float

In [75]:
a.left()

2.0

In [76]:
intersect(a,b)

('inner,outer,a.area,b.area: ', 7.5, 12.0, 10.5, 9.0)


True

## Reading xml files

There are 2 xml files. One with the ground truth and the other with the detected. Given the name of the image, need to get the boxes list from one, and the box list from other xml.

In [77]:
def getDetectedBoxes(image_file_name, xml_tree_root):
    """
    Get list of boxes detected given the name of the image and the path to the XML file.
    """
    
    #debug
    #print(start_time)
    #print("reading from: ", path_detector_xml_file)
    
    start_time = time.time()
    for image in xml_tree_root.iter('image'):
        #image found
        if image.attrib['file'] == image_file_name:
            if (len(image) == 0):
                return []
            else:
                list_boxes = []
                for box_num, box in enumerate(image):
                    box_attribs = box.attrib
#                     print(box.attrib)
                    box_rect = dlib.drectangle((float)(box_attribs['left']),
                                               (float)(box_attribs['top']),
                                              ((float)(box_attribs['left'])+(float)(box_attribs['width'])),
                                              ((float)(box_attribs['top'])+(float)(box_attribs['height'])))
                    list_boxes.append(box_rect)
#                 print("--- %s seconds ---" % (time.time() - start_time))
                return list_boxes
#     print('image not found')
    return None

In [78]:
def getListImagesFromXML(path_xml):
    """
    Gets the list of the image filenames from an XML
    """
    
    tree = ET.parse(path_xml)
    root = tree.getroot()
    
    list_filenames = []
    for image in root.iter('image'):
        list_filenames.append(image.attrib['file'])
        
    return list_filenames

## Getting Statistics

In [79]:
def getHitStats(list_images, path_truth_xml_file, path_detector_xml_file):
    """
    Get the statistics such as total_hits, correct_hits and total_true targets from a list of image names,
    and the path to xml files.
    """
    
    correct_hits = 0
    total_true_targets = 0
    missing_detections = 0
    total_hits = 0
    
    
    tree_truth = ET.parse(path_truth_xml_file)
    tree_truth_root = tree_truth.getroot()
    
    tree_detector = ET.parse(path_detector_xml_file)
    tree_detector_root = tree_detector.getroot()
    
    ignored_images = [] #To keep track of the images which are not present in either XML file

    for image in tqdm(list_images):
        
        true_boxes = getDetectedBoxes(image, tree_truth_root)
        detected_boxes = getDetectedBoxes(image, tree_detector_root)
        
        #If an image is not found in either XML, ignore that image and move forward
        if(true_boxes is None or detected_boxes is None):
            ignored_images.append(image)
            continue
        
#         print("detected rectangles: ",detected_boxes,"true rectangles: ", true_boxes)
        
        # If there are no boxes detected, add the true number of boxes to missing detections
        if (len(detected_boxes) == 0):
            missing_detections += len(true_boxes)
        
        # Go over all the labels (true boxes) and match them with all the detections.
        count = 0
        used = [False] * len(detected_boxes)
        for i in range(len(true_boxes)):
            
            #Compare a truth label with all the detected boxes, given that they are not yet detected/used
            found_match = False
            for j in range(len(detected_boxes)):
                
                if(used[j]):
                    continue
                
                if(intersect(true_boxes[i],detected_boxes[j])):
                    used[j] = True
                    found_match = True
                    count += 1
                    break
        
            if(not found_match):
                missing_detections += 1
        
        correct_hits += count
        total_true_targets += len(true_boxes)
        total_hits += used.count(True)
    print("Number of images ignored(not in either XML) are: ", len(ignored_images))
    print("total_hits, correct_hits, total_true_targets: ",total_hits, correct_hits, total_true_targets)
    return total_hits, correct_hits, total_true_targets    

In [80]:
def getAnalysis(total_hits, correct_hits, total_true_targets):
    """
    Get final precision and recall
    """
    
    if (total_hits == 0):
        precision = 1
    else:
        precision = float(correct_hits) / float(total_hits)
        
    if (total_true_targets == 0):
        recall = 1
    else:
        recall = float(correct_hits) / float(total_true_targets)
    print("total_hits, correct_hits, total_true_targets: ",total_hits, correct_hits, total_true_targets)
    print("precision, recall: ", precision, recall)
    return precision, recall

In [20]:
def main():
    list_images = getListImagesFromXML(path_openface_xml)
#     print(list_images[12:15])
    total_hits, correct_hits, total_true_targets = getHitStats(list_images, path_openface_xml,path_detector_1_xml)
    precision, recall = getAnalysis(total_hits, correct_hits, total_true_targets)
main()

  2%|▏         | 859/57234 [00:05<06:14, 150.63it/s]

image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found
image not found


  2%|▏         | 927/57234 [00:07<07:33, 124.20it/s]

image not found
image not found


  3%|▎         | 1541/57234 [00:09<05:40, 163.68it/s]

...

image not found
image not found
image not found
image not found


  5%|▌         | 3097/57234 [00:45<13:15, 68.10it/s]

image not found
image not found
image not found
image not found


  6%|▌         | 3182/57234 [00:47<13:27, 66.94it/s]

KeyboardInterrupt: 

In [ ]:
def main():
    list_images = getListImagesFromXML(path_openface_xml)
#     print(list_images[12:15])
    getHitStats(list_images, path_openface_xml,path_detector_2_xml)
main()

In [ ]:
def main():
    list_images = getListImagesFromXML(path_openface_xml)
#     print(list_images[12:15])
    getHitStats(list_images, path_openface_xml,path_detector_3_xml)
main()

In [96]:
getAnalysis(0, 13564, 39655)

('total_hits, correct_hits, total_true_targets: ', 0, 13564, 39655)
('precision, recall: ', 1, 0.3420501828268819)


(1, 0.3420501828268819)

#### Detector 1 results

('Number of images ignored(not in either XML) are: ', 7898)


('total_hits, correct_hits, total_true_targets: ', 0, 13564, 39655)

## Aggregating by Environment

In [81]:
path_folder_environment_sorted_videos = "/media/amogh/Stuff/CMU/datasets/bagamoyo_data/bagamoyo_videos/environment_sorted_videos/"

In [82]:
def getDicEnvironmentToListImages(path_folder_environment_sorted_videos, path_xml_all_boxes):
    """
    Gets dictionary of the form {env:[list_of_images]} different lists of images from xml depending on environment
    """
    
    dic_env_to_list_image_names = {}
    tree = ET.parse(path_xml_all_boxes)
    root = tree.getroot()
    list_filenames = []
    
    for image in root.iter('image'):
        list_filenames.append(image.attrib['file'])
    
    list_path_folder_environment = glob.glob(path_folder_environment_sorted_videos + '/*')
    # For each environment
    for path_folder_env in list_path_folder_environment:
        
        env_name = os.path.basename(path_folder_env)
        list_images_in_env = []
        list_path_videos = glob.glob(path_folder_env + '/*')
        # For each video in a particular environment
        for path_video in list_path_videos:
            video_name = os.path.basename(path_video)
            video_name_no_ext = os.path.splitext(video_name)[0]
            for filename_image in list_filenames:
                if(video_name_no_ext in filename_image):
                    list_images_in_env.append(filename_image)
        
        dic_env_to_list_image_names[env_name] = list_images_in_env
        print(len(list_images_in_env))
    return dic_env_to_list_image_names

In [83]:
def getHitStatsEnvWise(path_folder_environment_sorted_videos, path_truth_xml, path_detector_xml):
    """
    Publishes statistics(total_hots, correct_hits, total_true_targets, precision, recall) for different environments.
    
    Parameters
    ----------
    path_folder_environment_sorted_videos : str
        Path of the folder where different folders containing videos for each environment are
    
    path_truth_xml : str
        Path of the xml which would be used for truth labels
        
    path_detector_xml : str
        Path of the xml generated with custom detector
    
    Returns
    -------
    None
    
    """
    
    dic_env_to_list_image_names = getDicEnvironmentToListImages(path_folder_environment_sorted_videos, path_truth_xml)
    for env, list_images in dic_env_to_list_image_names.items():
        print("Starting environment: ", env )
        total_hits, correct_hits, total_true_targets = getHitStats(list_images, path_truth_xml,path_detector_xml)
        precision, recall = getAnalysis(total_hits, correct_hits, total_true_targets)

In [84]:
def main():
    getHitStatsEnvWise(path_folder_environment_sorted_videos, path_openface_xml, path_detector_1_xml)
main()

0
4192
26752
0
26290
('Starting environment: ', 'hut_background')




0it [00:00, ?it/s]



('Number of images ignored(not in either XML) are: ', 0)
('total_hits, correct_hits, total_true_targets: ', 0, 0, 0)
('total_hits, correct_hits, total_true_targets: ', 0, 0, 0)
('precision, recall: ', 1, 1)
('Starting environment: ', 'house_window_right')




  0%|          | 0/26752 [00:00<?, ?it/s]

  0%|          | 3/26752 [00:00<18:47, 23.72it/s]

  0%|          | 6/26752 [00:00<20:15, 22.01it/s]

  0%|          | 9/26752 [00:00<20:16, 21.98it/s]

  0%|          | 12/26752 [00:00<20:11, 22.07it/s]

  0%|          | 15/26752 [00:00<20:20, 21.90it/s]

  0%|          | 17/26752 [00:00<21:12, 21.01it/s]

  0%|          | 19/26752 [00:00<21:32, 20.69it/s]

  0%|          | 21/26752 [00:01<21:55, 20.32it/s]

  0%|          | 24/26752 [00:01<21:43, 20.51it/s]

  0%|          | 26/26752 [00:01<21:48, 20.43it/s]

  0%|          | 29/26752 [00:01<21:39, 20.56it/s]

  0%|          | 31/26752 [00:01<21:49, 20.41it/s]

  0%|          | 33/26752 [00:01<21:57, 20.28it/s]

  0%|          | 35/26752 [00:01<22:16, 19.99it/s]

  0%|          | 37/26752 [00:01<22:29, 19.79it/s]

  0%|          | 39/26752 [00:01<22:39, 19.65it/s]

  0%|          | 41/26752 [00:02<23:40, 18.80it/s]

  0%|          | 43/26752 [00:02<23:54, 18.62it/s]

  0%|          | 45/26

  5%|▍         | 1320/26752 [00:19<06:20, 66.82it/s]

  5%|▍         | 1334/26752 [00:19<06:18, 67.18it/s]

  5%|▌         | 1347/26752 [00:19<06:16, 67.47it/s]

  5%|▌         | 1360/26752 [00:20<06:14, 67.78it/s]

  5%|▌         | 1373/26752 [00:20<06:12, 68.08it/s]

  5%|▌         | 1386/26752 [00:20<06:11, 68.37it/s]

  5%|▌         | 1399/26752 [00:20<06:09, 68.63it/s]

  5%|▌         | 1412/26752 [00:20<06:07, 68.91it/s]

  5%|▌         | 1425/26752 [00:20<06:06, 69.18it/s]

  5%|▌         | 1438/26752 [00:20<06:04, 69.45it/s]

  5%|▌         | 1451/26752 [00:20<06:02, 69.70it/s]

  5%|▌         | 1464/26752 [00:20<06:01, 69.96it/s]

  6%|▌         | 1476/26752 [00:21<06:00, 70.07it/s]

  6%|▌         | 1489/26752 [00:21<05:59, 70.32it/s]

  6%|▌         | 1501/26752 [00:21<05:58, 70.50it/s]

  6%|▌         | 1512/26752 [00:22<06:08, 68.52it/s]

  6%|▌         | 1521/26752 [00:22<06:17, 66.75it/s]

  6%|▌         | 1528/26752 [00:23<06:25, 65.45it/s]

  6%|▌         | 1533/26752 

...

 98%|█████████▊| 25847/26290 [50:41<00:52,  8.50it/s]

 98%|█████████▊| 25848/26290 [50:42<00:52,  8.50it/s]

 98%|█████████▊| 25849/26290 [50:42<00:51,  8.50it/s]

 98%|█████████▊| 25850/26290 [50:42<00:51,  8.50it/s]

 98%|█████████▊| 25851/26290 [50:42<00:51,  8.50it/s]

 98%|█████████▊| 25852/26290 [50:42<00:51,  8.50it/s]

 98%|█████████▊| 25853/26290 [50:42<00:51,  8.50it/s]

 98%|█████████▊| 25854/26290 [50:42<00:51,  8.50it/s]

 98%|█████████▊| 25855/26290 [50:42<00:51,  8.50it/s]

 98%|█████████▊| 25856/26290 [50:42<00:51,  8.50it/s]

 98%|█████████▊| 25857/26290 [50:43<00:50,  8.50it/s]

 98%|█████████▊| 25858/26290 [50:43<00:50,  8.50it/s]

 98%|█████████▊| 25859/26290 [50:43<00:50,  8.50it/s]

 98%|█████████▊| 25860/26290 [50:43<00:50,  8.50it/s]

 98%|█████████▊| 25861/26290 [50:43<00:50,  8.50it/s]

 98%|█████████▊| 25862/26290 [50:43<00:50,  8.50it/s]

 98%|█████████▊| 25863/26290 [50:43<00:50,  8.50it/s]

 98%|█████████▊| 25864/26290 [50:43<00:50,  8.50it/s]

 98%|█████

 99%|█████████▉| 25981/26290 [50:57<00:36,  8.50it/s]

 99%|█████████▉| 25982/26290 [50:57<00:36,  8.50it/s]

 99%|█████████▉| 25983/26290 [50:57<00:36,  8.50it/s]

 99%|█████████▉| 25984/26290 [50:57<00:36,  8.50it/s]

 99%|█████████▉| 25985/26290 [50:57<00:35,  8.50it/s]

 99%|█████████▉| 25986/26290 [50:57<00:35,  8.50it/s]

 99%|█████████▉| 25987/26290 [50:57<00:35,  8.50it/s]

 99%|█████████▉| 25988/26290 [50:58<00:35,  8.50it/s]

 99%|█████████▉| 25989/26290 [50:58<00:35,  8.50it/s]

 99%|█████████▉| 25990/26290 [50:58<00:35,  8.50it/s]

 99%|█████████▉| 25991/26290 [50:58<00:35,  8.50it/s]

 99%|█████████▉| 25992/26290 [50:58<00:35,  8.50it/s]

 99%|█████████▉| 25993/26290 [50:58<00:34,  8.50it/s]

 99%|█████████▉| 25994/26290 [50:58<00:34,  8.50it/s]

 99%|█████████▉| 25995/26290 [50:58<00:34,  8.50it/s]

 99%|█████████▉| 25996/26290 [50:58<00:34,  8.50it/s]

 99%|█████████▉| 25997/26290 [50:59<00:34,  8.50it/s]

 99%|█████████▉| 25998/26290 [50:59<00:34,  8.50it/s]

 99%|█████

 99%|█████████▉| 26116/26290 [51:12<00:20,  8.50it/s]

 99%|█████████▉| 26117/26290 [51:12<00:20,  8.50it/s]

 99%|█████████▉| 26118/26290 [51:12<00:20,  8.50it/s]

 99%|█████████▉| 26119/26290 [51:13<00:20,  8.50it/s]

 99%|█████████▉| 26120/26290 [51:13<00:20,  8.50it/s]

 99%|█████████▉| 26121/26290 [51:13<00:19,  8.50it/s]

 99%|█████████▉| 26122/26290 [51:13<00:19,  8.50it/s]

 99%|█████████▉| 26123/26290 [51:13<00:19,  8.50it/s]

 99%|█████████▉| 26124/26290 [51:13<00:19,  8.50it/s]

 99%|█████████▉| 26125/26290 [51:13<00:19,  8.50it/s]

 99%|█████████▉| 26126/26290 [51:13<00:19,  8.50it/s]

 99%|█████████▉| 26127/26290 [51:13<00:19,  8.50it/s]

 99%|█████████▉| 26128/26290 [51:14<00:19,  8.50it/s]

 99%|█████████▉| 26129/26290 [51:14<00:18,  8.50it/s]

 99%|█████████▉| 26130/26290 [51:14<00:18,  8.50it/s]

 99%|█████████▉| 26131/26290 [51:14<00:18,  8.50it/s]

 99%|█████████▉| 26132/26290 [51:14<00:18,  8.50it/s]

 99%|█████████▉| 26133/26290 [51:14<00:18,  8.50it/s]

 99%|█████

100%|█████████▉| 26250/26290 [51:30<00:04,  8.49it/s]

100%|█████████▉| 26251/26290 [51:30<00:04,  8.49it/s]

100%|█████████▉| 26252/26290 [51:31<00:04,  8.49it/s]

100%|█████████▉| 26253/26290 [51:31<00:04,  8.49it/s]

100%|█████████▉| 26254/26290 [51:31<00:04,  8.49it/s]

100%|█████████▉| 26255/26290 [51:31<00:04,  8.49it/s]

100%|█████████▉| 26256/26290 [51:31<00:04,  8.49it/s]

100%|█████████▉| 26257/26290 [51:31<00:03,  8.49it/s]

100%|█████████▉| 26258/26290 [51:31<00:03,  8.49it/s]

100%|█████████▉| 26259/26290 [51:31<00:03,  8.49it/s]

100%|█████████▉| 26260/26290 [51:32<00:03,  8.49it/s]

100%|█████████▉| 26261/26290 [51:32<00:03,  8.49it/s]

100%|█████████▉| 26262/26290 [51:32<00:03,  8.49it/s]

100%|█████████▉| 26263/26290 [51:32<00:03,  8.49it/s]

100%|█████████▉| 26264/26290 [51:32<00:03,  8.49it/s]

100%|█████████▉| 26265/26290 [51:32<00:02,  8.49it/s]

100%|█████████▉| 26266/26290 [51:32<00:02,  8.49it/s]

100%|█████████▉| 26267/26290 [51:33<00:02,  8.49it/s]

100%|█████

('Number of images ignored(not in either XML) are: ', 3030)
('total_hits, correct_hits, total_true_targets: ', 13467, 13467, 21483)
('total_hits, correct_hits, total_true_targets: ', 13467, 13467, 21483)
('precision, recall: ', 1.0, 0.626867755900014)


**('Starting environment: ', 'house_window_right')**

('Number of images ignored(not in either XML) are: ', 4506)

('total_hits, correct_hits, total_true_targets: ', 26, 26, 14704)

('total_hits, correct_hits, total_true_targets: ', 26, 26, 14704)

('precision, recall: ', 1.0, 0.0017682263329706202)

**('Starting environment: ', 'house_window_at_back')**

('Number of images ignored(not in either XML) are: ', 362)

('total_hits, correct_hits, total_true_targets: ', 71, 71, 3468)

('total_hits, correct_hits, total_true_targets: ', 71, 71, 3468)

('precision, recall: ', 1.0, 0.020472895040369088)

**('Starting environment: ', 'library')**

('Number of images ignored(not in either XML) are: ', 3030)

('total_hits, correct_hits, total_true_targets: ', 13467, 13467, 21483)

('total_hits, correct_hits, total_true_targets: ', 13467, 13467, 21483)

('precision, recall: ', 1.0, 0.626867755900014)